In [1]:
import numpy as np
from scipy.linalg import sqrtm, logm
import mne

class GenerateurDonnees:
    def __init__(self, channels=3, sfreq=256.0, duration=10, change=5.0, A1=2.0e-6, A2=0.0e-6, sd=2.0e-6):
        self.channels = channels
        self.sfreq = sfreq
        self.duration = duration
        self.change = change
        self.frequencies = 10.0 + 2.0 * np.random.rand(channels)
        self.phases = 2.0 * np.pi * np.random.rand(channels)
        self.A1 = A1
        self.A2 = A2
        self.sd = sd
        self.info = mne.create_info([f'EEG{n:03}' for n in range(1, channels + 1)],
                                    ch_types=['eeg'] * channels, sfreq=sfreq)

    def generer_donnees(self):
        samples = int(self.sfreq * self.duration)
        t = np.linspace(0, self.duration, samples, endpoint=False)
        A = self.A1 + (t > self.change).astype(float) * (self.A2 - self.A1)
        data = A * np.cos(np.outer(self.frequencies, t) + np.outer(self.phases, np.ones(samples)))
        data += np.random.normal(0, self.sd, size=(self.channels, samples))
        # Vérification des valeurs infinies ou NaN
        if not np.isfinite(data).all():
            raise ValueError("Les données générées contiennent des valeurs infinies ou NaN")
        raw = mne.io.RawArray(data, self.info)
        return raw

    def exporter_donnees(self, filename='dummy.edf'):
        raw = self.generer_donnees()
        mne.export.export_raw(filename, raw, fmt='edf', overwrite=True)

In [ ]:
import numpy as np

class CovarianceCalculator:
    def __init__(self, X, l, s):
        """
        Initialiser avec les données X, la longueur des segments l, et le décalage s.
        X : numpy array où les lignes sont les variables et les colonnes sont les échantillons.
        """
        self.X = X
        self.l = l
        self.s = s
        self.C = []
        self.calculate_covariance_matrices()
    
    def calculate_covariance_matrices(self):
        """
        Calculer les matrices de covariance successives à partir des données initiales.
        """
        m = self.X.shape[1]  # nombre de colonnes (échantillons)
        n = (m - self.l) // self.s + 1
        
        for k in range(n):
            start_idx = k * self.s
            end_idx = start_idx + self.l
            segment = self.X[:, start_idx:end_idx]
            cov_matrix = np.cov(segment)
            self.C.append(cov_matrix)
    
    def add_new_data(self, new_X):
        """
        Ajouter de nouvelles matrices de covariance à partir de nouvelles données.
        new_X : numpy array où les lignes sont les variables et les colonnes sont les échantillons.
        """
        m = new_X.shape[1]  # nombre de colonnes (échantillons)
        n = (m - self.l) // self.s + 1
        
        for k in range(n):
            start_idx = k * self.s
            end_idx = start_idx + self.l
            segment = new_X[:, start_idx:end_idx]
            cov_matrix = np.cov(segment)
            self.C.append(cov_matrix)

# Exemple d'utilisation
if __name__ == "__main__":
    # Exemple de données initiales
    generateur = GenerateurDonnees()
    X_raw = generateur.generer_donnees()
    X = X_raw.get_data()
    l = 20  # longueur des segments
    s = 10  # décalage entre les segments

    # Créer une instance de la classe et calculer les matrices de covariance
    calc = CovarianceCalculator(X, l, s)
    print("Matrices de covariance initiales:")
    for cov in calc.C:
        print(cov)


In [14]:
from scipy.linalg import sqrtm, logm

class Transformation:
    def __init__(self):
        pass

    def project_to_tangent(self, cov_matrix_current, cov_matrix_next):
        sqrt_B = sqrtm(cov_matrix_next)
        sqrt_inv_B = np.linalg.inv(sqrt_B)
        transformed_A = np.dot(np.dot(sqrt_inv_B, cov_matrix_current), sqrt_inv_B)
        log_transformed_A = logm(transformed_A)
        return log_transformed_A

    def transport_to_tangent(self, delta_matrix, tangent_plane_start, tangent_plane_end):
        inv_B = np.linalg.inv(tangent_plane_end)
        A_invB = np.dot(tangent_plane_start, inv_B)
        E = sqrtm(A_invB)
        transported_Delta = np.dot(np.dot(E, delta_matrix), E.T)
        return transported_Delta


In [15]:
class Trajectory:
    def __init__(self, covariance_matrices):
        """
        Initialiser avec une liste de matrices de covariance.
        """
        self.C = covariance_matrices
        self.transformation = Transformation()
        self.Deltas = self.calculate_deltas()

    def calculate_deltas(self):
        """
        Calculer les incréments et les transports successifs pour reconstruire la trajectoire.
        """
        Deltas = {}
        n = len(self.C)
        
        # Calcul des projections directes
        for i in range(n - 1):
            Deltas[(i, i+1)] = self.transformation.project_to_tangent(self.C[i], self.C[i+1])

        # Calcul des transports successifs
        for i in range(n - 1):
            for j in range(i + 2, n):
                Deltas[(i, j)] = self.transformation.transport_to_tangent(Deltas[(i, j-1)], self.C[j-1], self.C[j])

        return Deltas

    def get_delta(self, i, j):
        """
        Obtenir l'incrément ∆i,j
        """
        return self.Deltas.get((i, j), None)


In [17]:
if __name__ == "__main__":
    # Exemple de données initiales
    generateur = GenerateurDonnees()
    X_raw = generateur.generer_donnees()
    X = X_raw.get_data()
    l = 20  # longueur des segments
    s = 10  # décalage entre les segments

    # Créer une instance de la classe et calculer les matrices de covariance
    calc = CovarianceCalculator(X, l, s)
    
    # Créer une instance de Trajectory pour calculer les trajectoires à partir des matrices de covariance
    traj = Trajectory(calc.C)
    
    # Afficher les deltas calculés
    for key, delta in traj.Deltas.items():
        print(f"Delta {key}:")
        print(delta)



Creating RawArray with float64 data, n_channels=3, n_times=2560
    Range : 0 ... 2559 =      0.000 ...     9.996 secs
Ready.
Delta (0, 1):
[[ 0.6245889  -0.4040066  -0.02583469]
 [-0.4040066   0.28885838  0.18590264]
 [-0.02583469  0.18590264 -0.08311693]]
Delta (1, 2):
[[-0.17493051  0.47906505  0.61731402]
 [ 0.47906505 -0.43864862 -0.15366919]
 [ 0.61731402 -0.15366919  0.19196723]]
Delta (2, 3):
[[-0.25863552 -0.25592069 -0.36411483]
 [-0.25592069  0.27541682 -0.02714468]
 [-0.36411483 -0.02714468  0.15933906]]
Delta (3, 4):
[[ 0.54115447 -0.02612534 -0.32549889]
 [-0.02612534  0.13501473 -0.07620191]
 [-0.32549889 -0.07620191  0.52892742]]
Delta (4, 5):
[[-0.01859857 -0.06031714  0.12165468]
 [-0.06031714 -0.68412775  0.03008172]
 [ 0.12165468  0.03008172 -0.27104254]]
Delta (5, 6):
[[-0.25782794  0.07515562 -0.11774109]
 [ 0.07515562  0.06650074  0.1759608 ]
 [-0.11774109  0.1759608  -0.25355336]]
Delta (6, 7):
[[-0.07517883  0.28995185  0.15477865]
 [ 0.28995185  1.29175325 -0.